# Data Preparation
Tento notebook si klade za cíl připravit data ze zdrojů a zdrojových systémů k dalšímu využití.

In [753]:
import pandas as pd
import numpy as np

## nahrání dat

In [754]:
links_data = pd.read_csv('../data_sources/links_data.csv')
municipality_codes = pd.read_csv('../data_sources/municipality_codes.csv')
ruian_data = pd.read_csv('../data_sources/ruian_data.csv')
stat_2022 = pd.read_csv('../data_sources/stat_obce_2022.csv', skiprows=[1])
stat_2023 = pd.read_csv('../data_sources/stat_obce_2023.csv', skiprows=[1])
uur_data = pd.read_csv('../data_sources/uur_data.csv')

## finalizace základního datového souboru

In [755]:
plans_municipalities_df = links_data.merge(municipality_codes, on='up_record_id', how='left')

In [756]:
plans_municipalities_df = plans_municipalities_df[plans_municipalities_df['format'] == 'application/pdf']
plans_municipalities_df = plans_municipalities_df.drop(columns=['name','type','format', 'doc_order', 'url_legend','is_full','date','map_url','created_date'])

In [757]:
plans_municipalities_df = plans_municipalities_df.dropna(subset=['municipality_kod'])
plans_municipalities_df['record_number'] = (plans_municipalities_df['up_record_id'].str.split('_').str[1]).astype(int)


In [758]:
plans_municipalities_df = plans_municipalities_df.sort_values('record_number').drop_duplicates(subset='municipality_kod', keep='first')


In [759]:
ruian_data = ruian_data.rename(columns={'KOD': 'municipality_kod'})
ruian_data['NAZEV'] = (
    ruian_data['NAZEV']
    .str.replace('č', 'é', regex=False)
    .str.replace('ø', 'ř', regex=False)
    .str.replace('Ø', 'Ř', regex=False)
    .str.replace('ì', 'ě', regex=False)
    .str.replace('Ì', 'Ě', regex=False)
    .str.replace('ò', 'ň', regex=False)
    .str.replace('Ò', 'Ň', regex=False)
    .str.replace('', 'ť', regex=False)
    .str.replace('Ý', 'Ť', regex=False)
    .str.replace('È', 'Č', regex=False)
    .str.replace('è', 'č', regex=False)
    .str.replace('ï', 'ď', regex=False)
)

In [760]:
plans_municipalities_df = plans_municipalities_df.merge(ruian_data, on='municipality_kod', how='left')
plans_municipalities_df['kraj'] = plans_municipalities_df['up_record_id'].str.split('_').str[0]
plans_municipalities_df = plans_municipalities_df.drop(columns=['CLENENI_SM_ROZSAH_KOD', 'CLENENI_SM_TYP_KOD', 'PLATI_OD', 'PLATI_DO', 'DATUM_VZNIKU', 'up_record_id', 'record_number', 'STATUS_KOD'])

In [761]:
plans_municipalities_df = plans_municipalities_df.rename(columns={'NAZEV': 'obec', 'POU_KOD': 'pou_kod', 'OKRES_KOD': 'okres_kod'})


In [762]:
new_order = [
    'obec',
    'kraj',
    'url',
    'municipality_kod',
    'pou_kod',
    'okres_kod',
]
plans_municipalities_df = plans_municipalities_df[new_order]
municipality_index_df = plans_municipalities_df[['obec', 'url', 'municipality_kod']]

In [763]:
stat_2022 = stat_2022[[
    'kód obce číslo',
    'název územní jednotky', 
    'KRAJ',
    'OKRES',
    'Počet obyvatel',
    'Přirozený přírůstek (osoba)', 
    'Přírůstek stěhováním (osoba)',
    'Počet obyvatel ve věku 0-14 let ',
    'Počet obyvatel ve věku 15-64 let',
    'Počet obyvatel ve věku 65 a více let',
    'Příjmy rozpočtů obcí celkem\n(tis. Kč)',
    'Výdaje\nrozpočtů\nobcí\ncelkem\n(tis. Kč)',
    'Počet dokončených bytů',
    'Počet hromadných ubytovacích zařízení celkem',
    'Podíl nezaměstna-\nných osob (%)',
    'Živě narození',
    'Zemřelí',
    'Přistěhovalí',
    'Vystěhovalí',
    'Zemědělská půda (ha)',
    'Nezemědělská půda (ha)',
    'Koeficient ekologické stability',
    'Průměrný věk',
    ]]

In [764]:
stat_2023 = stat_2023[[
    'kód obce číslo',
    'název územní jednotky', 
    'KRAJ',
    'OKRES',
    'Počet obyvatel',
    'Přirozený přírůstek (osoba)', 
    'Přírůstek stěhováním (osoba)',
    'Počet obyvatel ve věku 0-14 let ',
    'Počet obyvatel ve věku 15-64 let',
    'Počet obyvatel ve věku 65 a více let',
    'Příjmy rozpočtů obcí celkem\n(tis. Kč)',
    'Výdaje\nrozpočtů\nobcí\ncelkem\n(tis. Kč)',
    'Počet dokončených bytů',
    'Počet hromadných ubytovacích zařízení celkem',
    'Podíl nezaměstna-\nných osob (%)',
    'Živě narození',
    'Zemřelí',
    'Přistěhovalí',
    'Vystěhovalí',
    'Zemědělská půda (ha)',
    'Nezemědělská půda (ha)',
    'Koeficient ekologické stability',
    'Průměrný věk',
    ]]

In [765]:
rename_helper = [
    'municipality_kod',
    'obec', 
    'kraj',
    'okres',
    'pocet_obyvatel',
    'prirozeny_prirustek', 
    'prirustek_stehovanim',
    'obyvatele_0_14',
    'obyvatele_15_64',
    'obyvatele_65',
    'prijmy',
    'vydaje',
    'dokoncene_byty',
    'ubytovaci_zarizeni',
    'nezamestnanost',
    'narozeni',
    'zemreli',
    'pristehovali',
    'vystehovali',
    'zemedelska_puda',
    'nezemedelska_puda',
    'prumerny_vek',
    'koeficient_ekologie',
]

stat_2022.columns = rename_helper
stat_2023.columns = rename_helper

In [766]:
def clean_columns(df):
    for col in df.columns:
        if col != 'obec':
            df[col] = df[col].replace('-', '', regex=False)
    return df

clean_columns(stat_2022)
clean_columns(stat_2023)

municipality_kod                               obec                kraj  \
0               554782                              Praha  Hlavní město Praha   
1               529303                            Benešov         Středočeský   
2               532924                           Bukovany         Středočeský   
3               529451                           Bystřice         Středočeský   
4               529478                              Čakov         Středočeský   
5               529516                            Čerčany         Středočeský   
6               529541                    Český Šternberk         Středočeský   
7               529567                           Čtyřkoly         Středočeský   
8               529621                            Divišov         Středočeský   
9               532151                         Drahňovice         Středočeský   
10              529745                         Hvězdonice         Středočeský   
11              532886                          Chářovice         Středočeský   
12              532878                             Chleby         Středočeský   
13              532045                           Chlístov         Středočeský   
14              529796                          Chocerady         Středočeský   
15              532606                          Choratice         Středočeský   
16              529818                          Chotýšany         Středočeský   
17              532037                          Chrášťany         Středočeský   
18              529940                            Kozmice         Středočeský   
19              529958                           Krhanice         Středočeský   
20              529974                             Krňany         Středočeský   
21              529991                          Křečovice         Středočeský   
22              530051                             Lešany         Středočeský   
23              532258                        Litichovice         Středočeský   
24              532193                             Lštění         Středočeský   
25              530115                          Maršovice         Středočeský   
26              530204                               Mrač         Středočeský   
27              530263                            Nespeky         Středočeský   
28              530298                          Netvořice         Středočeský   
29              530310                           Neveklov         Středočeský   
30              530352                           Ostředek         Středočeský   
31              530409                          Petroupim         Středočeský   
32              532649                           Popovice         Středočeský   
33              530441                 Poříčí nad Sázavou         Středočeský   
34              530450                          Postupice         Středočeský   
35              530492                Přestavlky u Čerčan         Středočeský   
36              538680                             Pyšely         Středočeský   
37              530522                             Rabyně         Středočeský   
38              538710                           Řehenice         Středočeský   
39              534382                             Sázava         Středočeský   
40              530638                           Soběhrdy         Středočeský   
41              599379                            Stranný         Středočeský   
42              530689                          Struhařov         Středočeský   
43              530760                        Teplýšovice         Středočeský   
44              532592                              Tisem         Středočeský   
45              532304                          Třebešice         Středočeský   
46              530841                  Týnec nad Sázavou         Středočeský   
47              532061                          Václavice         Středočeský   
48              532614               

In [767]:
def append_suffix_to_columns(df: pd.DataFrame, keep: int, suffix: str) -> pd.DataFrame:
    columns = df.columns.tolist()
    unchanged = columns[:keep]
    modified = [c + f'{suffix}' for c in columns[keep:]]
    df.columns = unchanged + modified
    return df

In [768]:
stat_2022 = append_suffix_to_columns(stat_2022, keep=4, suffix='_2022')
stat_2023 = append_suffix_to_columns(stat_2023, keep=4  , suffix='_2023')

In [769]:
stat_2022_mergable = stat_2022.drop(columns=['obec', 'kraj', 'okres'])
stat_2023_mergable = stat_2023.drop(columns=['obec', 'kraj', 'okres'])

In [770]:
final_df_enriched = plans_municipalities_df.merge(stat_2023_mergable, on='municipality_kod', how='left')
final_df_enriched = final_df_enriched.merge(stat_2022_mergable, on='municipality_kod', how='left')

In [771]:
final_df_enriched = final_df_enriched.replace(',', '', regex=True)

In [772]:
uur_data['Obec'] = uur_data['Obec'].fillna(uur_data['Unnamed: 1'])

In [773]:
uur_data = uur_data.drop(columns=['Unnamed: 1', 'Druh dokumentace', 'Číslo dokumentace'])
uur_data['Návrh - nabytí účinnosti 117'] = uur_data['Návrh - nabytí účinnosti 117'].fillna(uur_data['Návrh – vydání / schválení 116'])
uur_data['Návrh - nabytí účinnosti 117'] = uur_data['Návrh - nabytí účinnosti 117'].fillna(uur_data['Návrh – stanovisko krajského úřadu / nadřízeného orgánu územního plánování 115'])
uur_data['Návrh - nabytí účinnosti 117'] = uur_data['Návrh - nabytí účinnosti 117'].fillna(uur_data['Návrh - zahájení projednání 113'])
uur_data['Návrh - nabytí účinnosti 117'] = uur_data['Návrh - nabytí účinnosti 117'].fillna(uur_data['Návrh - odevzdání 112'])
uur_data['Návrh - nabytí účinnosti 117'] = uur_data['Návrh - nabytí účinnosti 117'].fillna(uur_data['Zadání - schválení 105'])
uur_data['Návrh - nabytí účinnosti 117'] = uur_data['Návrh - nabytí účinnosti 117'].fillna(uur_data['Zadání - ukončení projednání 104'])
uur_data['Návrh - nabytí účinnosti 117'] = uur_data['Návrh - nabytí účinnosti 117'].fillna(uur_data['Zadání - zahájení projednání 103'])
uur_data['Návrh - nabytí účinnosti 117'] = uur_data['Návrh - nabytí účinnosti 117'].fillna(uur_data['Zahájení prací - schválení / rozhodnutí o pořízení 101'])


In [774]:
uur_data = uur_data[['Obec', 'Název dokumentace', 'Návrh - nabytí účinnosti 117']]
uur_data = uur_data.rename(columns={'Obec': 'obec', 'Název dokumentace': 'posledni_dokumentace', 'Návrh - nabytí účinnosti 117': 'posledni_dokumentace_datum'})

In [775]:
uur_data['posledni_dokumentace_datum'] = pd.to_datetime(uur_data['posledni_dokumentace_datum'])
uur_data = uur_data.sort_values('posledni_dokumentace_datum', ascending=False).drop_duplicates(subset='obec', keep='first')

C:\Users\torte\AppData\Local\Temp\ipykernel_22560\2912811581.py:1: UserWarning: Parsing dates in %d.%m.%Y format when dayfirst=False (the default) was specified. Pass `dayfirst=True` or specify a format to silence this warning.
  uur_data['posledni_dokumentace_datum'] = pd.to_datetime(uur_data['posledni_dokumentace_datum'])


In [776]:
uur_data['posledni_dokumentace_datum'] = uur_data['posledni_dokumentace_datum'].dt.strftime('%Y-%m')

In [777]:
final_df_enriched = final_df_enriched.merge(uur_data, on='obec', how='left')

In [778]:
final_df_enriched = final_df_enriched.dropna(subset=['posledni_dokumentace_datum'])
final_df_enriched['municipality_kod'] = final_df_enriched['municipality_kod'].astype(int)

In [779]:
for i in range(1, 6):
    final_df_enriched[f'trend_{i}'] = ''
    final_df_enriched[f'problem_{i}'] = ''

In [780]:
final_df_enriched.to_csv('../cleansed_data/municipalities.csv', index=False, encoding='utf-8-sig')
municipality_index_df.to_csv('../cleansed_data/municipalities_links.csv', index=False, encoding='utf-8-sig')